# E10-3: A multi-resolution sinusoidal model

In this exercise you will implement a multi-resolution sine model by modifying the `sineModel()` function. 

You have seen through several assignments that the choice of window size is an important tradeoff between time and frequency resolution. Longer windows have a better frequency resolution and can resolve two close sinusoids even at low frequencies, while smaller windows have a better time resolution leading to sharper onsets. So far, in all the analyses, we have only considered a single window length over the whole sound. As we know, analysis of signals with low frequency components needs longer windows as compared to signals with high frequency content. The optimal choice of window length is thus dependent on the frequency content of the signal. In other words, it is better to choose a longer window for the analysis of the low frequencies while a shorter window is sufficient for higher frequencies. In this exercise, you will explore the use of multiple window sizes for analysis in different frequency bands of the signals, what is called multi-resolution.

For each audio frame of `x` you should compute three different DFTs with three different window sizes and find the sinusoidal peaks for each of the DFTs. For example, you can choose window sizes `M1 = 4095, M2 = 2047, M3 = 1023`, to generate three windows w1, w2, w3. Choose N1, N2, N3 to be the power of two bigger than the corresponding window size. Then compute the spectra, `X1`, `X2`, and `X3` using `dftAnal()`. Define the frequency bands like `B1: 0 <= f < 1000Hz, B2: 1000 <= f < 5000, B3: 5000 <= f < 22050` and find the peaks of `B1` in `X1`, the ones of `B2` in `X2`, and the ones of `B3` in `X3`. From the peaks we finally re-synthesize the frame and generate the output `y`. 

Complete `sineModelMultiRes()`, by copiying and modifying the code from `SineModel()`. The functions should take as input three windows with different sizes, three FFT sizes, and the values for the frequency bands. Write the code to implement the multi-resolution analysis as described above.

Choose two different polyphonic recordings from freesound that have both a relevant melodic and percussion components. Edit them and change their format as needed. Choose suitable set of parameters for their analysis. Experiment with different window sizes and fruequency bands for the two sounds such that you get both crisp onsets and good frequency resolution. Get the best posible base line reconstruction with `SineModel()` and the best with `sineModelMultiRes()`. Listen the sounds and visualize the information that might be needed to undertand the process. 

Your explanation should include:

1. Freesound link to the two sounds chosen.
2. Explanation and justification of the band edges and the window sizes for each sound.
3. Observations about the advantages of a multi-resolution analysis (comment on the time-frequency resolution, computational complexity and extensions to HPR and HPS models).
4. Challenges you might face if you were to extend it to HPR and HPS models (mainly in sinusoid tracking and F0 estimation).
5. Further methods to improving the time-frequency resolution trade-off. 


In [1]:
import sys, os
from scipy.signal import get_window
import numpy as np
from scipy.signal import blackmanharris, triang
from scipy.fftpack import ifft, fftshift, fft
import math
sys.path.append('../software/models/')
import dftModel as DFT
import utilFunctions as UF
import dftModel as DFT
import utilFunctions as UF
import sineModel as SM
import IPython.display as ipd
import time

For different window size, we have different hM1,hM2,pin,pend.  
            e.g. If w1 = 100, w2 = 400, then first pin1 = 50, first pin2 = 200. But we must select one pin for all      windows, to analyze frequencies occuring same time. Solutions;     
            __1)__ Ignore beginning and end of the sound for small windows. Set pin = 200, small window (100) will cover x(pin-50:pin+50); pin-50=100; first 100 samples for small window is gone.    
            __2)__ Keep pin2(big window) waiting, until pin1(small window) reaches pin2, at the   beginning. And at the end, when pin2 hits the end of samples earlier, hold it again and keep pin1 incrementing.  
            __3)__ Apply zero padding to samples and go with first way. 

In [2]:
# N boundaries instead of 3
# Current sound pointer method from above: 3, padding done externally
def sineModelMultiRes(x, fs, w, N, t, B):
    """
    Analysis/synthesis of a sound using the sinusoidal model, without sine tracking
    Inputs:
        x: input array sound
        w: N analysis windows
        t: threshold in negative dB 
        B: N frequency boundaries
    Output:
        y: output array sound
    """
### your code here, start from copying the code from sineModel()
    
    if ((len(w)!=len(B))&(len(w)!=len(N))): 
        raise ValueError("number of windows, N and boundaries must be equal")
        
    Ns = 512                                                # FFT size for synthesis (even)
    H = Ns//4                                               # Hop size used for analysis and synthesis
    hNs = Ns//2                                             # half of synthesis FFT size
    yw = np.zeros(Ns)                                       # initialize output sound frame
    y = np.zeros(x.size)                                    # initialize output array
    sw = np.zeros(Ns)                                       # initialize synthesis window
    ow = triang(2*H)                                        # triangular window
    sw[hNs-H:hNs+H] = ow                                    # add triangular window
    bh = blackmanharris(Ns)                                 # blackmanharris window
    bh = bh / sum(bh)                                       # normalized blackmanharris window
    sw[hNs-H:hNs+H] = sw[hNs-H:hNs+H] / bh[hNs-H:hNs+H]     # normalized synthesis window
    
    hM1 = []
    hM2 = []
    pin_array = []
    pend_array = []
    for i in range (len(B)):    
        hM1.append(int(math.floor((w[i].size+1)/2)))        # half analysis window size by rounding
        hM2.append(int(math.floor(w[i].size/2)))            # half analysis window size by floor
        pin_array.append(max(hNs, hM1[i]))                  # init sound pointer in middle of anal window       
        pend_array.append(x.size - max(hNs, hM1[i]))        # last sample to start a frame
        w[i] = w[i] / sum(w[i])                             # normalize analysis windows
        
    pin = max(pin_array) # pin pend selection explained in cell above.
    pend = min(pend_array)
    while pin<pend:                             # while input sound pointer is within sound 
    #-----analysis-----
        iploc_array = np.array([])
        ipmag_array = np.array([])
        ipphase_array = np.array([])
        ipfreq_array = np.array([])
        for i in range (len(B)):
            x1 = x[pin-hM1[i]:pin+hM2[i]]                       # select frame
            mX, pX = DFT.dftAnal(x1, w[i], N[i])                # compute dft
            ploc = UF.peakDetection(mX, t)                      # detect locations of peaks
            ploc[np.logical_and(B[i][0]<(ploc*fs/N[i]),(ploc*fs/N[i])<=B[i][1])] # return the ploc corresp.to Band
            iploc, ipmag, ipphase = UF.peakInterp(mX, pX, ploc) # refine peak values by interpolation
                
            iploc_array = np.append(iploc_array,iploc)        # store plocs of each band
            ipmag_array = np.append(ipmag_array,ipmag)
            ipphase_array = np.append(ipphase_array,ipphase)
            ipfreq_array = np.append(ipfreq_array,fs*iploc/float(N[i]))  # convert peak locations to Hertz
        
    #-----synthesis-----
        Y = UF.genSpecSines(ipfreq_array, ipmag_array, ipphase_array, Ns, fs)   # generate sines in the spectrum         
        fftbuffer = np.real(ifft(Y))                          # compute inverse FFT
        yw[:hNs-1] = fftbuffer[hNs+1:]                        # undo zero-phase window
        yw[hNs-1:] = fftbuffer[:hNs+1] 
        y[pin-hNs:pin+hNs] += sw*yw                           # overlap-add and apply a synthesis window
        pin += H                                              # advance sound pointer
    return y

In [3]:
# base line sinusoidal analysis/synthesis
### set the parameters
input_file = '../sounds/chinese-orchestra-fragment.wav' #https://freesound.org/people/xserra/sounds/217543/

fs, x = UF.wavread(input_file)
M = 401
N = 2048
t = -85
window = 'blackman'

# no need to change code from here
fs, x = UF.wavread(input_file) 
w = get_window(window, M) 
y = SM.sineModel(x, fs, w, N, t)
ipd.display(ipd.Audio(data=x, rate=fs))
ipd.display(ipd.Audio(data=y, rate=fs))

In [4]:
M = [7001,3001,2001,901,401]
N = [8192,4096,4096,2048,2048]
t = -90
B = [(0,150),(150,500),(501,2000),(2001,5000), (5001,22050)]

window = 'blackman'
w_array = []
for i in range (len(M)):
    w = get_window(window, M[i])
    w_array.append(w)
xpad = np.pad(x,max(M)//2,mode='constant') 
# no need to change code from here
y = sineModelMultiRes(xpad, fs, w_array, N, t, B)
ipd.display(ipd.Audio(data=y, rate=fs))

In [5]:
ipd.display(ipd.Audio(data=x[22000:40000], rate=fs)) # Drums original

In [6]:
ipd.display(ipd.Audio(data=y[(max(M)//2)+22000:(max(M)//2)+40000], rate=fs)) # Drums

In [7]:
ipd.display(ipd.Audio(data=x[170000:250000], rate=fs)) # Trill original

In [8]:
ipd.display(ipd.Audio(data=y[(max(M)//2)+170000:(max(M)//2)+250000], rate=fs)) # Trill

In [26]:
# base line sinusoidal analysis/synthesis
### set the parameters
input_file = '../sounds/guitar-and-drums2.wav' #https://freesound.org/people/zagi2/sounds/439686/
M = 1201
N = 2048
t = -85
window = 'blackman'

# no need to change code from here
fs, x = UF.wavread(input_file) 
x = x[:x.size//2]
w = get_window(window, M) 
y = SM.sineModel(x, fs, w, N, t)
ipd.display(ipd.Audio(data=x, rate=fs))
ipd.display(ipd.Audio(data=y, rate=fs))

In [27]:
M = [4001,2701,1001,501]
N = [8192,4096,4096,2048]
t = -90
B = [(0,300),(301,2000),(2001,5000),(5001,22050)]

window = 'blackman'
w_array = []
for i in range (len(M)):
    w = get_window(window, M[i])
    w_array.append(w)
xpad = np.pad(x,max(M)//2,mode='constant')      # Reason of this padding is explained in second cell
# no need to change code from here
y = sineModelMultiRes(xpad, fs, w_array, N, t, B)
ipd.display(ipd.Audio(data=y, rate=fs))

In [11]:
ipd.display(ipd.Audio(data=x[22000:40000], rate=fs)) # muted strum original

In [28]:
ipd.display(ipd.Audio(data=y[22000:40000], rate=fs)) # muted strum

## Your explanation
    
sinModelMultiRes takes N boundaries and windows instead of 3   
B can be in format of (1000,2000,..) and boundaries can be (0<f<B1, B1<f<B2) but the next approach is better.  
B will be ((b1,B1),(b2,B2)..) so we can select the frequencies we want, e.g. (1000<f<2000), (5000<f<6000)  
__1)__   
https://freesound.org/people/zagi2/sounds/439686/  
https://freesound.org/people/xserra/sounds/217543/   

__2)__  
All band edge and window size decisions come from the observations on two( high freq & time res.) STFTs.  
Window sizes considered for K=6 and K=2.02(if blackman). Then optimized by listening.    
  
Chinese orchestra sound: https://freesound.org/people/xserra/sounds/217543/  
Keeping the timbre and onset of the drum same time was difficult  
Drum has mainly low frequencies but there are also high frequency parts.   
  
b1,B1 = 0,150 , W=7001 ;  6*fs/13 = 20k, 2.02*fs/13 = 6852     
b2,B2 = 151,500, W=3001 ; 6*fs/30 = 8820, 2.02*fs/30 = 2969   
b3,B3 = 501,2000, W=2001 ; 6*fs/50 = 5292, 2.02*fs/50 = 1781    
b4,B4 = 2001,5000, W=901 ; 6*fs/100 = 2646, 2.02*fs/100 = 890   
b5,B5 = 5001,22050, W=401 ;, 6*fs/250 = 1058, 2.02*fs/250 = 356     
  
  
When large window (>10k) is used for low freqs, they are smeared. Even though high freqs are sharp, they are not   perceived as onsets of the drum, because high freqs have lesser magnitude and (I believe) they are masked by   smeared low freqs. Also magnitude of low freq band increases more, due to picking of more peaks when window is   large.  
  
When window size of low band is lowered (still higher than other bands), onsets are more perceivable but with some loss on magnitude of low band. Still much better than sineModel() anyway. 

Guitar and drum sound, https://freesound.org/people/zagi2/sounds/439686/  
To keep the sound natural, we may want to have high time resolution at muted strums. Because in original track we  can feel the order of string plucked. But to do that without losing frequency resolution of guitar chords, we have to implement multi resolution across time. 

b1,B1 = 0,300 , W=4001 ;  6*fs/30= 8820, 2.02*fs/30 = 2969.4  ; kick  
b2,B2 = (301,2000) W=2701; 6*fs/100 = 2646, 2.02*fs/100 = 890  ; lowest chord  
b3,B3 = (2001,5000) W=1001; 6*fs/100 = 2646, 2.02*fs/100 = 890 ; peaks are still close but W is lower to capture   onsets.   
 
__3)__   
MultiRes model we can select time and frequency resolutions for each frequency band we describe. We can use this   to preserve onsets and timbre quality at the same time. We may also set those resolutions according to our   perception (e.g JND in frequency). Computation time is close to sum of sineModel analysis for each M.  
  
Chinese orchestra sound execution times:    
sineModel M:1201 N:2048, 1.2s    
MultiRes (values above), 10.81s    
     
sineModel M:7001 N:8192  4.265s     
sineModel M:3001 N:4096  2.29    
sineModel M:2001 N:4096  1.9    
sineModel M:901 N:2048  1.08s    
sineModel M:401 N:2048  0.85s ;  sum=10.385, Complexity: O(MultiRes) = sum( O(sineModel) for each M )   
  
__4)__  
In harmonic models, we calculate f0 by looking at all of the harmonics of f0 candidates. Thus having a low freq resolution on higher bands will affect selected f0. Another restriction is, range of f0 better be on one freq band. Otherwise, error threshold (f0et) will cause different sine tracking behaviours for different bands.   
  
__5)__    
The chinese orchestra sound ends with a trill. That trill will require more time resolution than before. Increasing time resolution for whole freq band for that trill is not beneficial. MultiResolution should also include time options, so window sizes and freq. bands can be changed along time. Deciding all those values will be tiresome, maybe we can do it automatically.

I think there is a problem at frequencies near boundaries. Let's say we have a boundary at 1kHz. W is large for below, small for above. Large window can detect a peak at 990Hz, and small window can detect the exact peak at 1010Hz, due to locations of bins and how the energy is spread across the bins. Both of those peaks will be accepted in this implementation.  
Maybe we can use overlapping boundaries and merge very close peaks.


In [13]:
def hprModelMultiRes(x, fs, w, B, N, t, nH, minf0, maxf0, f0et):  # B is added
    """
    Analysis/synthesis of a sound using the harmonic plus residual model
    x: input sound, fs: sampling rate, w: analysis window, 
    N: FFT size (minimum 512), t: threshold in negative dB,    Array
    nH: maximum number of harmonics, minf0: minimum f0 frequency in Hz, 
    maxf0: maximim f0 frequency in Hz, 
    f0et: error threshold in the f0 detection (ex: 5),
    maxhd: max. relative deviation in harmonic detection (ex: .2)
    returns y: output sound, yh: harmonic component, xr: residual component
    """
    if ((len(w)!=len(B))&(len(w)!=len(N))): 
        raise ValueError("number of windows, N and boundaries must be equal")
        
    #hN = N//2                                                     # size of positive spectrum
    #hM1 = int(math.floor((w.size+1)/2))                           # half analysis window size by rounding
    #hM2 = int(math.floor(w.size/2))                               # half analysis window size by floor
    Ns = 512                                                      # FFT size for synthesis (even)
    H = Ns//4                                                     # Hop size used for analysis and synthesis
    hNs = Ns//2      
    # pin = max(hNs, hM1)                                           # initialize sound pointer in middle of analysis window          
    # pend = x.size - max(hNs, hM1)                                 # last sample to start a frame
    #fftbuffer = np.zeros(N)                                       # initialize buffer for FFT
    yhw = np.zeros(Ns)                                            # initialize output sound frame
    xrw = np.zeros(Ns)                                            # initialize output sound frame
    yh = np.zeros(x.size)                                         # initialize output array
    xr = np.zeros(x.size)                                         # initialize output array
    # w = w / sum(w)                                                # normalize analysis window
    sw = np.zeros(Ns)     
    ow = triang(2*H)                                              # overlapping window
    sw[hNs-H:hNs+H] = ow      
    bh = blackmanharris(Ns)                                       # synthesis window
    bh = bh / sum(bh)                                             # normalize synthesis window
    wr = bh                                                       # window for residual
    sw[hNs-H:hNs+H] = sw[hNs-H:hNs+H] / bh[hNs-H:hNs+H]
    hfreqp = []
    f0t = 0
    f0stable = 0    
    
    hM1 = []
    hM2 = []
    pin_array = []
    pend_array = []
    for i in range (len(B)):    
        hM1.append(int(math.floor((w[i].size+1)/2)))        # half analysis window size by rounding
        hM2.append(int(math.floor(w[i].size/2)))            # half analysis window size by floor
        pin_array.append(max(hNs, hM1[i]))                  # init sound pointer in middle of anal window       
        pend_array.append(x.size - max(hNs, hM1[i]))        # last sample to start a frame
        w[i] = w[i] / sum(w[i])                             # normalize analysis windows
        
    pin = max(pin_array) 
    pend = min(pend_array)
    
    while pin<pend:  
    #-----analysis-----             
        iploc = np.array([])
        ipmag = np.array([])
        ipphase = np.array([])
        ipfreq = np.array([])
        for i in range (len(B)):
            x1 = x[pin-hM1[i]:pin+hM2[i]]                       # select frame
            mX, pX = DFT.dftAnal(x1, w[i], N[i])                # compute dft
            ploc = UF.peakDetection(mX, t)                      # detect locations of peaks
            ploc[np.logical_and(B[i][0]<(ploc*fs/N[i]),(ploc*fs/N[i])<=B[i][1])] # return the ploc corresp.to Band
            iploc_t, ipmag_t, ipphase_t = UF.peakInterp(mX, pX, ploc) # refine peak values by interpolation
            
            iploc = np.append(iploc,iploc_t)        # store plocs of each band
            ipmag = np.append(ipmag,ipmag_t)
            ipphase = np.append(ipphase,ipphase_t)
            ipfreq = np.append(ipfreq,fs*iploc_t/float(N[i]))
            
        f0t = UF.f0Twm(ipfreq, ipmag, f0et, minf0, maxf0, f0stable) # find f0
        if ((f0stable==0)&(f0t>0)) \
            or ((f0stable>0)&(np.abs(f0stable-f0t)<f0stable/5.0)):
            f0stable = f0t                                            # consider a stable f0 if it is close to the previous one
        else:
            f0stable = 0                
        hfreq, hmag, hphase = HM.harmonicDetection(ipfreq, ipmag, ipphase, f0t, nH, hfreqp, fs) # find harmonics
        hfreqp = hfreq
        ri = pin-hNs-1                                             # input sound pointer for residual analysis
        xw2 = x[ri:ri+Ns]*wr                                       # window the input sound                     
        fftbuffer = np.zeros(Ns)                                   # reset buffer
        fftbuffer[:hNs] = xw2[hNs:]                                # zero-phase window in fftbuffer
        fftbuffer[hNs:] = xw2[:hNs]                     
        X2 = fft(fftbuffer)                                        # compute FFT of input signal for residual analysis
        #-----synthesis-----
        Yh = UF.genSpecSines(hfreq, hmag, hphase, Ns, fs)          # generate sines
        Xr = X2-Yh                                                 # get the residual complex spectrum                       
        fftbuffer = np.zeros(Ns)
        fftbuffer = np.real(ifft(Yh))                              # inverse FFT of harmonic spectrum
        yhw[:hNs-1] = fftbuffer[hNs+1:]                            # undo zero-phase window
        yhw[hNs-1:] = fftbuffer[:hNs+1] 
        fftbuffer = np.zeros(Ns)
        fftbuffer = np.real(ifft(Xr))                              # inverse FFT of residual spectrum
        xrw[:hNs-1] = fftbuffer[hNs+1:]                            # undo zero-phase window
        xrw[hNs-1:] = fftbuffer[:hNs+1]
        yh[ri:ri+Ns] += sw*yhw                                     # overlap-add for sines
        xr[ri:ri+Ns] += sw*xrw                                     # overlap-add for residual
        pin += H                                                   # advance sound pointer
    y = yh+xr                                                    # sum of harmonic and residual components
    return y, yh, xr

In [14]:
import harmonicModel as HM
input_file = '../sounds/piano.wav'
fs, x = UF.wavread(input_file)


M = [1001,3001,2001,2001,1001]
N = [2048,4096,4096,2048,2048]
t = -90
B = [(0,100),(100,300),(301,2400),(2401,5000), (5001,22050)]

window = 'blackman'
w_array = []
for i in range (len(M)):
    w = get_window(window, M[i])
    w_array.append(w)
xpad = np.pad(x,max(M)//2,mode='constant')  

minf0 = 100
maxf0 = 300
f0et = 10
nH = 50
y, yh, xr = hprModelMultiRes(xpad, fs, w_array, B, N, t, nH, minf0, maxf0, f0et)

ipd.display(ipd.Audio(data=xpad, rate=fs))
ipd.display(ipd.Audio(data=y, rate=fs))

ipd.display(ipd.Audio(data=yh, rate=fs))
ipd.display(ipd.Audio(data=xr, rate=fs))